# Properites of Returns and Volatility
January 2025

*Imports*

In [1]:
from datetime import date
import yfinance as yf
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
from statsmodels.tsa.stattools import acf,pacf
import plotly.graph_objects as go
from plotly.subplots import make_subplots
from scipy.stats import skew, kurtosis, kstest
from statsmodels.stats.diagnostic import het_arch

import itertools
from statsmodels.tsa.arima.model import ARIMA
from arch import arch_model

ModuleNotFoundError: No module named 'yfinance'

*Data*

In [2]:
# Parameters
start_date = date(2015,1,1)
end_date = date(2025,1,1)
tickers = ['AAPL','SPY','IBM','TSLA']

# Retrieve Data
df = yf.download(tickers=tickers,
                 start=start_date,end=end_date,auto_adjust=True)['Close']

volume = yf.download(tickers=tickers,
                 start=start_date,end=end_date,auto_adjust=True)['Volume']

# Calculate Returns
returns = (np.log(df)
           .diff()
           .dropna()
        )

[*********************100%***********************]  4 of 4 completed
[*********************100%***********************]  4 of 4 completed


### **Returns**

#### 1. Lagged Auto-correlations are small

In [3]:
fig = make_subplots(rows=1, cols=4,
                    subplot_titles=returns.columns)

for i, col in enumerate(returns.columns):
    _acf = pacf(returns[col],nlags=20)

    fig.add_trace(
        go.Scatter(
            y=_acf,
            name=f"{col} ACF",
            mode='markers',
            marker=dict(color = 'black'),
            showlegend=False,
        ),
        row=1,
        col=i + 1,
    )

    for lag in range(len(_acf)):
        fig.add_trace(
            go.Scatter(
                x=[lag, lag], 
                y=[0, _acf[lag]],
                mode='lines',
                line=dict(color='black'),
                showlegend=False,
            ),
            row=1,
            col=i + 1,
        )

fig.update_layout(title = 'Log Return ACF Plots (2015/1/1-2025/1/1)')
fig.update_xaxes(title = 'Lag')
fig.update_yaxes(title = 'ACF')
fig.show()

#### 2. Heavy Tails

In [4]:
def bootstrap_dist(data, func, n_bootstrap=1000):

    bootstrap_stats = []
    for _ in range(n_bootstrap):
        sample = np.random.choice(data, size=len(data), replace=True)
        bootstrap_stats.append(func(sample))
    return bootstrap_stats

def compute_stats(df, n_bootstrap=1000, alpha=0.01):

    results = []
    for column in df.columns:
        data = df[column].dropna().values
        
        # Bootstrap distributions
        skew_bootstrap = bootstrap_dist(data, skew, n_bootstrap)
        kurt_bootstrap = bootstrap_dist(data, lambda x: kurtosis(x, fisher=True), n_bootstrap)
        
        # Compute mean, lower CI, and upper CI for skewness
        skew_mean = np.mean(skew_bootstrap)
        skew_lower = np.percentile(skew_bootstrap, alpha / 2 * 100)
        skew_upper = np.percentile(skew_bootstrap, (1 - alpha / 2) * 100)
        
        # Compute mean, lower CI, and upper CI for kurtosis
        kurt_mean = np.mean(kurt_bootstrap)
        kurt_lower = np.percentile(kurt_bootstrap, alpha / 2 * 100)
        kurt_upper = np.percentile(kurt_bootstrap, (1 - alpha / 2) * 100)
        
        # Append results
        results.append({
            'Column': column,
            'Skewness Mean': skew_mean,
            'Skewness CI (lower)': skew_lower,
            'Skewness CI (upper)': skew_upper,
            'Kurtosis Mean': kurt_mean,
            'Kurtosis CI (lower)': kurt_lower,
            'Kurtosis CI (upper)': kurt_upper,
        })
    return pd.DataFrame(results)

# Compute stats
results = compute_stats(returns, n_bootstrap=1000, alpha=0.01)
results.round(1)

Column  Skewness Mean  Skewness CI (lower)  Skewness CI (upper)  \
0   AAPL           -0.2                 -0.9                  0.4   
1    IBM           -0.7                 -1.8                  0.2   
2    SPY           -0.8                 -2.2                  0.4   
3   TSLA           -0.0                 -0.6                  0.4   

   Kurtosis Mean  Kurtosis CI (lower)  Kurtosis CI (upper)  
0            5.3                  2.7                  8.6  
1           10.4                  6.1                 16.0  
2           13.2                  4.8                 22.0  
3            4.4                  2.8                  6.2

#### 3. Autocorrelation of absolute returns and second moments

**Absolute Returns**

In [5]:
fig = make_subplots(rows=1, cols=4,
                    subplot_titles=returns.columns)

for i, col in enumerate(returns.columns):
    _acf = acf(abs(returns[col]),nlags=20)

    fig.add_trace(
        go.Scatter(
            y=_acf,
            name=f"{col} ACF",
            mode='markers',
            marker=dict(color = 'black'),
            showlegend=False,
        ),
        row=1,
        col=i + 1,
    )

    for lag in range(len(_acf)):
        fig.add_trace(
            go.Scatter(
                x=[lag, lag], 
                y=[0, _acf[lag]],
                mode='lines',
                line=dict(color='black'),
                showlegend=False,
            ),
            row=1,
            col=i + 1,
        )

fig.update_layout(title = 'Absolute Log Return ACF Plots (2015/1/1-2025/1/1)')
fig.update_xaxes(title = 'Lag')
fig.update_yaxes(title = 'ACF')
fig.show()

**Second Moments**

In [6]:
fig = make_subplots(rows=1, cols=4,
                    subplot_titles=returns.columns)

for i, col in enumerate(returns.columns):
    _acf = pacf(returns[col]**2,nlags=20)

    fig.add_trace(
        go.Scatter(
            y=_acf,
            name=f"{col} ACF",
            mode='markers',
            marker=dict(color = 'black'),
            showlegend=False,
        ),
        row=1,
        col=i + 1,
    )

    for lag in range(len(_acf)):
        fig.add_trace(
            go.Scatter(
                x=[lag, lag], 
                y=[0, _acf[lag]],
                mode='lines',
                line=dict(color='black'),
                showlegend=False,
            ),
            row=1,
            col=i + 1,
        )

fig.update_layout(title = 'Square Log Return ACF Plots (2015/1/1-2025/1/1)')
fig.update_xaxes(title = 'Lag')
fig.update_yaxes(title = 'ACF')
fig.show()

#### 4. Aggregational Guassinaity

In [7]:
def resample_returns(df, frequency):
    return df.resample(frequency).sum()

def plot_histograms(daily, weekly, monthly, bins=30):

    assets = daily.columns
    n_assets = len(assets)
    titles = [[f'{asset} - Daily',f'{asset} - Weekly',f'{asset} - Monthly'] for asset in assets]
    title = [item for sublist in titles for item in sublist]
    
    fig = make_subplots(rows=n_assets, cols=3, subplot_titles= title)

    for i, asset in enumerate(assets):
        # Daily returns
        fig.add_trace(
            go.Histogram(x=daily[asset], nbinsx=bins, name=f"Daily - {asset}", opacity=0.7, marker=dict(color='blue')),
            row=i+1, col=1
        )
        
        # Weekly returns 
        fig.add_trace(
            go.Histogram(x=weekly[asset], nbinsx=bins, name=f"Weekly - {asset}", opacity=0.7, marker=dict(color='green')),
            row=i+1, col=2
        )
        
        # Monthly returns
        fig.add_trace(
            go.Histogram(x=monthly[asset], nbinsx=bins, name=f"Monthly - {asset}", opacity=0.7, marker=dict(color='red')),
            row=i+1, col=3
        )

    fig.update_layout(
        height=5 * n_assets*50,
        width=15*75,
        showlegend=False,
        title_text="Log Returns Distribution (2015.1.1-2025.1.1)",
        title_x=0.5,
        barmode='overlay',
    )
    fig.update_xaxes(title_text="Returns")
    fig.update_yaxes(title_text="Frequency")
    
    fig.show()


# Resample into weekly and monthly log returns
weekly_returns = resample_returns(returns, 'W')
monthly_returns = resample_returns(returns, 'ME')

# Plot
plot_histograms(returns[["AAPL",'SPY']], weekly_returns[["AAPL",'SPY']], monthly_returns[["AAPL",'SPY']], bins=35)

**KS Test**

In [8]:
results = {}

for col in returns.columns:
    if col not in results:
        results[col] = {}
    for freq, return_series in [('daily', returns), ('weekly', weekly_returns), ('monthly', monthly_returns)]:
        
        stat, p = kstest(return_series[col], 'norm', args=(return_series[col].mean(), return_series[col].std()))
        
        results[col][f"{freq.capitalize()} - Statistic"] = stat
        results[col][f"{freq.capitalize()} - p-value"] = p

ks_results_df = pd.DataFrame.from_dict(results, orient='index')

ks_results_df.astype(float).round(4)

Daily - Statistic  Daily - p-value  Weekly - Statistic  \
AAPL             0.0773              0.0              0.0535   
IBM              0.0887              0.0              0.0781   
SPY              0.1065              0.0              0.0811   
TSLA             0.0652              0.0              0.0479   

      Weekly - p-value  Monthly - Statistic  Monthly - p-value  
AAPL            0.0968               0.0800             0.4046  
IBM             0.0033               0.0639             0.6866  
SPY             0.0019               0.1100             0.1013  
TSLA            0.1765               0.0574             0.8021

### **Volatility**

#### 1. Volatility Clustering

In [9]:
fig = make_subplots(rows=4,cols=1,subplot_titles=returns.columns,
                    vertical_spacing=0.1
                    )

for i, col in enumerate(returns.columns):
    fig.add_trace(
        go.Scatter(
            x = returns.index,
            y = returns[col],
            name = col
        ),
        row = i+1,
        col = 1,
    )

fig.update_layout(title = "Log Return Time Series (2015.1.1 - 2025.1.1)",height=700)
fig.update_yaxes(title = 'Log Return')
fig.show()

In [10]:
fig = make_subplots(rows=4,cols=1,subplot_titles=returns.columns,
                    vertical_spacing=0.1
                    )

for i, col in enumerate(returns.columns):
    fig.add_trace(
        go.Scatter(
            x = returns.index,
            y = abs(returns[col]),
            name = col
        ),
        row = i+1,
        col = 1,
    )

fig.update_layout(title = "Absolute Log Return Time Series (2015.1.1 - 2025.1.1)",height=700)
fig.update_yaxes(title = 'Absolute Log Return')
fig.show()

In [11]:
fig = make_subplots(rows=4,cols=1,subplot_titles=returns.columns,
                    vertical_spacing=0.1
                    )

for i, col in enumerate(returns.columns):
    fig.add_trace(
        go.Scatter(
            x = returns.index,
            y = returns[col]**2,
            name = col
        ),
        row = i+1,
        col = 1,
    )

fig.update_layout(title = "Squared Log Return Time Series (2015.1.1 - 2025.1.1)",height=700)
fig.update_yaxes(title = 'Squared Log Return')
fig.show()

In [12]:
results = {}

for col in returns.columns:
    if col not in results:
        results[col] = {}
    for transformation, transformed_series in [
        ('Log Returns', returns[col]),
        ('Absolute Log Returns', abs(returns[col])),
        ('Squared Log Returns', returns[col]**2),
    ]:
        # Perform the ARCH-LM test
        arch_test_stat, arch_test_pvalue, _, _ = het_arch(transformed_series)
        
        # Store results
        results[col][f"{transformation} - Statistic"] = arch_test_stat
        results[col][f"{transformation} - p-value"] = arch_test_pvalue


arch_results_df = pd.DataFrame.from_dict(results, orient='index')
arch_results_df = arch_results_df.astype(float).round(4)

arch_results_df

Log Returns - Statistic  Log Returns - p-value  \
AAPL                 399.5459                    0.0   
IBM                  309.2905                    0.0   
SPY                  962.3081                    0.0   
TSLA                 144.7202                    0.0   

      Absolute Log Returns - Statistic  Absolute Log Returns - p-value  \
AAPL                          399.5459                             0.0   
IBM                           309.2905                             0.0   
SPY                           962.3081                             0.0   
TSLA                          144.7202                             0.0   

      Squared Log Returns - Statistic  Squared Log Returns - p-value  
AAPL                         425.3823                            0.0  
IBM                          220.2888                            0.0  
SPY                          820.3514                            0.0  
TSLA                          80.1797                            0.0

#### 2. The Leverage Effect

In [13]:
absolute_returns = returns.abs()

correlations = {}

for col in returns.columns:
    
    correlations[col] = {}
    for lag in range(-5, 5+1):  
        if lag < 0:
            lagged_volatility = absolute_returns[col].shift(-lag)
        else:
            
            lagged_volatility = absolute_returns[col].shift(lag)
        
        correlation_data = pd.DataFrame({
            'Returns': returns[col],
            'Lagged Volatility': lagged_volatility
        }).dropna()

        correlations[col][f"{lag}"] = correlation_data.corr().iloc[0, 1]

correlation_df = pd.DataFrame.from_dict(correlations, orient='index')
correlation_df = correlation_df.round(4)

correlation_df

-5      -4      -3      -2      -1       0       1       2       3  \
AAPL -0.0684  0.0008  0.0073 -0.0192 -0.0131 -0.0032 -0.0131 -0.0192  0.0073   
IBM  -0.0009 -0.0255  0.0066  0.0007 -0.0162 -0.1133 -0.0162  0.0007  0.0066   
SPY  -0.0551  0.0037 -0.0361 -0.0196 -0.0169 -0.1141 -0.0169 -0.0196 -0.0361   
TSLA -0.0034  0.0159  0.0624 -0.0517  0.0675  0.0281  0.0675 -0.0517  0.0624   

           4       5  
AAPL  0.0008 -0.0684  
IBM  -0.0255 -0.0009  
SPY   0.0037 -0.0551  
TSLA  0.0159 -0.0034

In [14]:
corr_df_long = correlation_df.T.reset_index().melt(id_vars=['index'])

fig = go.Figure()

for ticker in corr_df_long['variable'].unique():
    fig.add_trace(
        go.Scatter(
            x=corr_df_long.loc[corr_df_long['variable'] == ticker, 'index'],
            y=corr_df_long.loc[corr_df_long['variable'] == ticker, 'value'],
            mode='markers',
            name=ticker
        )
    )

fig.update_layout(title = 'Correlations between returns and volatility (2015.1.1 - 2025.1.1)')
fig.update_xaxes(title = 'Lag')
fig.update_yaxes(title = 'Corr')
fig.show()

#### 3. Volatility/Volume

In [15]:
abs_returns = returns.abs()

lags = range(-5, 5+1) 

correlation_results = []

for ticker in returns.columns:
    
    vol = volume[ticker]
    abs_ret = abs_returns[ticker]
    
    
    for lag in lags:
        if lag < 0:
            shifted_ret = abs_ret.shift(-lag)
        else:
            shifted_ret = abs_ret.shift(lag)
        
        combined_df = pd.DataFrame({'Volume': vol, 'Lagged_Abs_Returns': shifted_ret}).dropna()
        
        
        corr = combined_df['Volume'].corr(combined_df['Lagged_Abs_Returns'])
        
        
        correlation_results.append({
            'Ticker': ticker,
            'Lag': lag,
            'Correlation': corr
        })

correlation_df = pd.DataFrame(correlation_results)
correlation_df.head()

Ticker  Lag  Correlation
0   AAPL   -5     0.152863
1   AAPL   -4     0.168109
2   AAPL   -3     0.181115
3   AAPL   -2     0.202838
4   AAPL   -1     0.317260

In [16]:
fig = go.Figure()

for ticker in correlation_df['Ticker'].unique():
    fig.add_trace(
        go.Scatter(
            x=correlation_df.loc[correlation_df['Ticker'] == ticker, 'Lag'],
            y=correlation_df.loc[correlation_df['Ticker'] == ticker, 'Correlation'],
            mode='markers',
            name=ticker
        )
    )

fig.update_layout(title = 'Correlations between volatility and volume (2015.1.1 - 2025.1.1)')
fig.update_xaxes(title = 'Lag')
fig.update_yaxes(title = 'Corr')
fig.show()

### **Motivations for GARCH**

#### 1. ARMA

In [17]:
best_models = {}

p_values = range(0, 5) 
q_values = range(0, 5)

pq_combinations = list(itertools.product(p_values, q_values))

for ticker in returns.columns:
    best_aic = float('inf')
    best_order = None
    best_model = None

    # Try each combination of p and q
    for p, q in pq_combinations:
        try:
            # Fit ARMA model
            model = ARIMA(returns[ticker], order=(p, 0, q))
            fitted_model = model.fit()
            
            if fitted_model.aic < best_aic:
                best_aic = fitted_model.aic
                best_order = (p, q)
                best_model = fitted_model
        except Exception as e:
            # Handle any models that fail to fit
            print(f"Failed to fit ARMA({p},{q}) for {ticker}: {e}")
    if best_model:
        best_models[ticker] = {
            "model": best_model,
            "order": best_order,
            "aic": best_aic
        }

/Users/tomcole/github-projects/.venv/lib/python3.12/site-packages/statsmodels/tsa/base/tsa_model.py:473: ValueWarning:

A date index has been provided, but it has no associated frequency information and so will be ignored when e.g. forecasting.

/Users/tomcole/github-projects/.venv/lib/python3.12/site-packages/statsmodels/tsa/base/tsa_model.py:473: ValueWarning:

A date index has been provided, but it has no associated frequency information and so will be ignored when e.g. forecasting.

/Users/tomcole/github-projects/.venv/lib/python3.12/site-packages/statsmodels/tsa/base/tsa_model.py:473: ValueWarning:

A date index has been provided, but it has no associated frequency information and so will be ignored when e.g. forecasting.

/Users/tomcole/github-projects/.venv/lib/python3.12/site-packages/statsmodels/tsa/base/tsa_model.py:473: ValueWarning:

A date index has been provided, but it has no associated frequency information and so will be ignored when e.g. forecasting.

/Users/tomcole/g

In [18]:
pd.DataFrame(best_models).T[['order','aic']].rename(columns={'order':'Order','aic':"AIC"})

Order           AIC
AAPL  (0, 1) -13095.616441
IBM   (2, 2) -13996.757967
SPY   (3, 2) -15552.831298
TSLA  (2, 2)  -9599.545243

In [19]:
fig = make_subplots(rows=4,cols=1,subplot_titles=returns.columns,
                    vertical_spacing=0.1
                    )

for i, col in enumerate(returns.columns):
    fig.add_trace(
        go.Scatter(
            x = returns.index,
            y = best_models[col]['model'].resid,
            name = col + " ARMA" +  str(best_models[col]['order'])
        ),
        row = i+1,
        col = 1,
    )

fig.update_layout(title = "Residuals Time Series (2015.1.1 - 2025.1.1)",height=700)
fig.update_yaxes(title = 'Reisduals')
fig.show()

### 2. ARCH

In [20]:
best_arch_models = {}

for ticker in returns.columns:
    best_aic = float('inf')
    best_model = None
    best_order = None

    for q in range(1, 5):
        try:
            
            model = arch_model(returns[ticker], vol='ARCH', p=q)
            fitted_model = model.fit(disp="off")
            
            if fitted_model.aic < best_aic:
                best_aic = fitted_model.aic
                best_model = fitted_model
                best_order = q
        except Exception as e:
            print(f"Failed for {ticker} with lag {q}: {e}")

    best_arch_models[ticker] = {'model': best_model, 'order': best_order, 'aic': best_aic}

/Users/tomcole/github-projects/.venv/lib/python3.12/site-packages/arch/univariate/base.py:309: DataScaleWarning:

y is poorly scaled, which may affect convergence of the optimizer when
estimating the model parameters. The scale of y is 0.0003214. Parameter
estimation work better when this value is between 1 and 1000. The recommended
rescaling is 100 * y.

This warning can be disabled by either rescaling y before initializing the
model or by setting rescale=False.


/Users/tomcole/github-projects/.venv/lib/python3.12/site-packages/arch/univariate/base.py:309: DataScaleWarning:

y is poorly scaled, which may affect convergence of the optimizer when
estimating the model parameters. The scale of y is 0.0003214. Parameter
estimation work better when this value is between 1 and 1000. The recommended
rescaling is 100 * y.

This warning can be disabled by either rescaling y before initializing the
model or by setting rescale=False.


/Users/tomcole/github-projects/.venv/lib/python3.12/site-pac

In [21]:
pd.DataFrame(best_arch_models).T[['order','aic']].rename(columns={"order":'Order','aic':'AIC'})

Order           AIC
AAPL     4 -13450.043907
IBM      4 -14268.345528
SPY      4 -16621.882437
TSLA     4  -9812.740752

In [22]:
fig = make_subplots(rows=4,cols=1,subplot_titles=returns.columns,
                    vertical_spacing=0.1
                    )

for i, col in enumerate(returns.columns):
    fig.add_trace(
        go.Scatter(
            x = returns.index,
            y = best_arch_models[col]['model'].resid,
            name = col + " ARCH(" +  str(best_arch_models[col]['order']) + ")"
        ),
        row = i+1,
        col = 1,
    )

fig.update_layout(title = "Residuals Time Series (2015.1.1 - 2025.1.1)",height=700)
fig.update_yaxes(title = 'Reisduals')
fig.show()

### 3. GARCH

In [23]:
best_garch_models = {}

for ticker in returns.columns:
    best_aic = float('inf')
    best_model = None
    best_order = None

    for p in range(1, 5): 
        for q in range(1, 5):
            try:
                
                model = arch_model(returns[ticker], vol='GARCH', p=p, q=q)
                fitted_model = model.fit(disp="off")
                
                if fitted_model.aic < best_aic:
                    best_aic = fitted_model.aic
                    best_model = fitted_model
                    best_order = (p, q)
            except Exception as e:
                print(f"Failed for {ticker} with (p, q) = ({p}, {q}): {e}")
    best_garch_models[ticker] = {'model': best_model, 'order': best_order,'aic' : best_aic}

/Users/tomcole/github-projects/.venv/lib/python3.12/site-packages/arch/univariate/base.py:309: DataScaleWarning:

y is poorly scaled, which may affect convergence of the optimizer when
estimating the model parameters. The scale of y is 0.0003214. Parameter
estimation work better when this value is between 1 and 1000. The recommended
rescaling is 100 * y.

This warning can be disabled by either rescaling y before initializing the
model or by setting rescale=False.


/Users/tomcole/github-projects/.venv/lib/python3.12/site-packages/arch/univariate/base.py:309: DataScaleWarning:

y is poorly scaled, which may affect convergence of the optimizer when
estimating the model parameters. The scale of y is 0.0003214. Parameter
estimation work better when this value is between 1 and 1000. The recommended
rescaling is 100 * y.

This warning can be disabled by either rescaling y before initializing the
model or by setting rescale=False.


/Users/tomcole/github-projects/.venv/lib/python3.12/site-pac

In [24]:
pd.DataFrame(best_garch_models).T[['order','aic']].rename(columns={"order":'Order','aic':'AIC'})

Order           AIC
AAPL  (1, 2)  -13576.28994
IBM   (1, 1) -14303.409436
SPY   (1, 1) -16692.518707
TSLA  (1, 1)  -9928.350846

In [25]:
fig = make_subplots(rows=4,cols=1,subplot_titles=returns.columns,
                    vertical_spacing=0.1
                    )

for i, col in enumerate(returns.columns):
    fig.add_trace(
        go.Scatter(
            x = returns.index,
            y = best_garch_models[col]['model'].resid,
            name = col + " GARCH" +  str(best_garch_models[col]['order'])
        ),
        row = i+1,
        col = 1,
    )

fig.update_layout(title = "Residuals Time Series (2015.1.1 - 2025.1.1)",height=700)
fig.update_yaxes(title = 'Reisduals')
fig.show()

### 4. Comparison

In [26]:
arma_df = pd.DataFrame(best_models).T[['order','aic']].rename(columns={'order':'Order','aic':"AIC"})
arma_df['Model'] = 'ARMA'

arch_df = pd.DataFrame(best_arch_models).T[['order','aic']].rename(columns={"order":'Order','aic':'AIC'})
arch_df['Model'] = 'ARCH'

garch_df = pd.DataFrame(best_garch_models).T[['order','aic']].rename(columns={"order":'Order','aic':'AIC'})
garch_df['Model'] = 'GARCH'

aic_df = pd.concat([arma_df,arch_df,garch_df])

In [27]:
aic_df = aic_df.reset_index().rename(columns = {'index':'Ticker'})
aic_df

Ticker   Order           AIC  Model
0    AAPL  (0, 1) -13095.616441   ARMA
1     IBM  (2, 2) -13996.757967   ARMA
2     SPY  (3, 2) -15552.831298   ARMA
3    TSLA  (2, 2)  -9599.545243   ARMA
4    AAPL       4 -13450.043907   ARCH
5     IBM       4 -14268.345528   ARCH
6     SPY       4 -16621.882437   ARCH
7    TSLA       4  -9812.740752   ARCH
8    AAPL  (1, 2)  -13576.28994  GARCH
9     IBM  (1, 1) -14303.409436  GARCH
10    SPY  (1, 1) -16692.518707  GARCH
11   TSLA  (1, 1)  -9928.350846  GARCH

In [28]:
fig = go.Figure()

for model in aic_df['Model'].unique():
    fig.add_trace(
        go.Scatter(
            x = aic_df.loc[aic_df['Model'] == model, 'Ticker'],
            y = aic_df.loc[aic_df['Model'] == model, 'AIC'],
            mode = 'markers',
            name = model
        )
    )
fig.update_layout(title = 'AIC by Ticker and Model')
fig.update_yaxes(title = 'AIC')
fig.update_xaxes(title = 'Ticker')
fig.show()